In [1]:
# Swing Trade Algorithm

In [2]:
# !pip install alpaca-trade-api

In [3]:
#Import Required Libraries

import os
import requests
import pandas as pd
import hvplot.pandas
import numpy as np
from dotenv import load_dotenv
import alpaca_trade_api as tradeapi
from pathlib import Path


In [4]:
#Load .env environment variables

# load_dotenv()

In [5]:
# Set Alpaca API Key 

# alpaca_api_key = os.getenv('ALPACA_API_KEY')
#alpaca_secret_key = os.getenv('ALPACA_SECRET_KEY')


In [6]:
# Creae the API object

#alpaca = tradeapi.REST(
   # alpaca_api_key,
   # alpaca_secret_key,
   # api_version='V2')

    

In [7]:
# Format current date as ISO format

#start_date = pd.Timestamp('2010-01-01', tz='America/New_York').isoformat()
#end_date= pd.Timestamp('2021-09-01', tz='America/New_York').isoformat()


# Set the tickers 

#SPY = ['SPY']
#QQQ = ['QQQ']
#AAPL = ['AAPL']
#NVDA = ['NVDA']
#TWTR = ['TWTR']

    

In [8]:
# Set timeframe to one day ('1D') for the Alpaca API
#timeframe = '15Min'

# Get current closing prices for SPY

#SPY_df = alpaca.get_barset(
  #  SPY,
  #  timeframe,
  #  start = start_date,
   # end = end_date,
   # limit=1000
#).df

# Display SPY df 

#display(SPY_df.head())
#display(SPY_df.tail())

In [9]:
# Read in the CSV data for SPY

SPY_df = pd.read_csv(Path('./Resources/SPY_Close.csv'),
                     index_col='Date',
                     parse_dates=True,
                     infer_datetime_format=True)

SPY_df.head()

Open     Close
Date                          
1993-01-29  43.96875  43.93750
1993-02-01  43.96875  44.25000
1993-02-02  44.21875  44.34375
1993-02-03  44.40625  44.81250
1993-02-04  44.96875  45.00000

In [10]:
# Create df for SPY closing prices

SPY_close = pd.DataFrame()

SPY_close['close'] = SPY_df['Close']

# Drop the time component of the date

# SPY_close.index = SPY_close.index.time

# Review SPY DF

display(SPY_close.head())
display(SPY_close.tail())


close
Date                
1993-01-29  43.93750
1993-02-01  44.25000
1993-02-02  44.34375
1993-02-03  44.81250
1993-02-04  45.00000

close
Date                  
2021-09-03  453.079987
2021-09-07  451.459991
2021-09-08  450.910004
2021-09-09  448.980011
2021-09-10  445.440002

In [11]:
SPY_signals = pd.DataFrame()


SPY_signals['close'] = SPY_close['close']
SPY_signals['returns'] = SPY_close['close'].pct_change()

SPY_signals = SPY_signals.dropna()

SPY_signals.head()

close   returns
Date                          
1993-02-01  44.25000  0.007112
1993-02-02  44.34375  0.002119
1993-02-03  44.81250  0.010571
1993-02-04  45.00000  0.004184
1993-02-05  44.96875 -0.000694

In [12]:
# Set the short window and long window
short_window = 6
long_window = 9

# Generate the fast and slow simple moving averages 
SPY_signals['SMA_Fast'] = SPY_signals['close'].rolling(window=short_window).mean()
SPY_signals['SMA_Slow'] = SPY_signals['close'].rolling(window=long_window).mean()

SPY_signals = SPY_signals.dropna()

# Review the DataFrame
display(SPY_signals.head())
display(SPY_signals.tail())

SPY_signals["signal"] = 0.0

close   returns   SMA_Fast   SMA_Slow
Date                                                
1993-02-11  44.93750  0.004892  44.875000  44.739583
1993-02-12  44.59375 -0.007650  44.807292  44.777778
1993-02-16  43.46875 -0.025228  44.557292  44.680556
1993-02-17  43.43750 -0.000719  44.302083  44.527778
1993-02-18  43.40625 -0.000719  44.093750  44.350694

close   returns    SMA_Fast    SMA_Slow
Date                                                    
2021-09-03  453.079987 -0.000243  452.018331  450.583333
2021-09-07  451.459991 -0.003576  452.219996  450.971110
2021-09-08  450.910004 -0.001218  451.999995  451.193332
2021-09-09  448.980011 -0.004280  451.569997  451.495555
2021-09-10  445.440002 -0.007885  450.510000  450.961110

In [13]:
# Generate the trading signal 0 or 1,
# where 1 is the short-window (SMA6) greater than the long-window (SMA9)
# and 0 is when the condition is not met
SPY_signals["signal"][short_window:] = np.where(
    SPY_signals["SMA_Slow"][short_window:] > SPY_signals["SMA_Fast"][short_window:], 1.0, 0.0
)

# Review the DataFrame
SPY_signals.tail(10)

close   returns    SMA_Fast    SMA_Slow  signal
Date                                                            
2021-08-27  450.250000  0.008941  447.335002  445.232222     0.0
2021-08-30  452.230011  0.004398  448.813339  446.142222     0.0
2021-08-31  451.559998 -0.001482  449.530004  447.517778     0.0
2021-09-01  451.799988  0.000531  450.168335  448.844445     0.0
2021-09-02  453.190002  0.003077  450.881668  449.936669     0.0
2021-09-03  453.079987 -0.000243  452.018331  450.583333     0.0
2021-09-07  451.459991 -0.003576  452.219996  450.971110     0.0
2021-09-08  450.910004 -0.001218  451.999995  451.193332     0.0
2021-09-09  448.980011 -0.004280  451.569997  451.495555     0.0
2021-09-10  445.440002 -0.007885  450.510000  450.961110     1.0

In [14]:
# Initialize the new Signal column
# SPY_signals['signal'] = 0.0

# When Actual Returns are greater than or equal to 0, generate signal to buy stock long
#SPY_signals.loc[(SPY_signals['returns'] >= 0), 'signal'] = 1

# When Actual Returns are less than 0, generate signal to sell 
# SPY_signals.loc[(SPY_signals['returns'] < 0), 'signal'] = -1

# Review the DataFrame
#display(SPY_signals.head())
# display(SPY_signals.tail())

In [15]:
# Initiate the value count

SPY_signals['signal'].value_counts()

0.0    4212
1.0    2986
Name: signal, dtype: int64

In [16]:
# Calculate the strategy returns and add them to the signals_df DataFrame
SPY_signals['strategy_returns'] = SPY_signals['returns'] * SPY_signals['signal'].shift()

# Review the DataFrame
display(SPY_signals.head())
display(SPY_signals.tail())

close   returns   SMA_Fast   SMA_Slow  signal  strategy_returns
Date                                                                          
1993-02-11  44.93750  0.004892  44.875000  44.739583     0.0               NaN
1993-02-12  44.59375 -0.007650  44.807292  44.777778     0.0              -0.0
1993-02-16  43.46875 -0.025228  44.557292  44.680556     0.0              -0.0
1993-02-17  43.43750 -0.000719  44.302083  44.527778     0.0              -0.0
1993-02-18  43.40625 -0.000719  44.093750  44.350694     0.0              -0.0

close   returns    SMA_Fast    SMA_Slow  signal  \
Date                                                               
2021-09-03  453.079987 -0.000243  452.018331  450.583333     0.0   
2021-09-07  451.459991 -0.003576  452.219996  450.971110     0.0   
2021-09-08  450.910004 -0.001218  451.999995  451.193332     0.0   
2021-09-09  448.980011 -0.004280  451.569997  451.495555     0.0   
2021-09-10  445.440002 -0.007885  450.510000  450.961110     1.0   

            strategy_returns  
Date                          
2021-09-03              -0.0  
2021-09-07              -0.0  
2021-09-08              -0.0  
2021-09-09              -0.0  
2021-09-10              -0.0

In [17]:
(1 + SPY_signals[['strategy_returns','returns']]).cumprod().hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [18]:
# Calculate the points in time when the Signal value changes
# Identify trade entry (1) and exit (-1) points
SPY_signals["entry/exit"] = SPY_signals["signal"].diff()

# Review the DataFrame
SPY_signals.loc["2020-02-09":"2020-02-17"]

close   returns    SMA_Fast    SMA_Slow  signal  \
Date                                                               
2020-02-10  334.679993  0.007465  331.149999  329.214444     0.0   
2020-02-11  335.260010  0.001733  333.006668  330.174445     0.0   
2020-02-12  337.420013  0.006443  334.400004  331.256670     0.0   
2020-02-13  337.059998 -0.001067  335.100006  332.960002     0.0   
2020-02-14  337.600006  0.001602  335.703339  334.457781     0.0   

            strategy_returns  entry/exit  
Date                                      
2020-02-10               0.0         0.0  
2020-02-11               0.0         0.0  
2020-02-12               0.0         0.0  
2020-02-13              -0.0         0.0  
2020-02-14               0.0         0.0

In [19]:
# Set initial capital for backtesting
initial_capital = float(1000000)

# Set the share size
share_size = 5000

In [20]:
# Buy a 5000 share position when the dual moving average crossover Signal equals 1 (SMA6 is greater than SMA9)
# Sell a 5000 share position when the dual moving average crossover Signal equals 0 (SMA6 is less than SMA9)
SPY_signals['position'] = share_size * SPY_signals['signal']

In [21]:
# Determine the points in time where a 5000 share position is bought or sold
SPY_signals['entry/exit_position'] = SPY_signals['position'].diff()

In [22]:
# Multiply the close price by the number of shares held, or the Position
SPY_signals['portfolio_holdings'] = SPY_signals['close'] * SPY_signals['position']

In [23]:
# Subtract the amount of either the cost or proceeds of the trade from the initial capital invested
SPY_signals['portfolio_cash'] = initial_capital - (SPY_signals['close'] * SPY_signals['entry/exit_position']).cumsum()

In [24]:
# Calculate the total portfolio value by adding the portfolio cash to the portfolio holdings (or investments)
SPY_signals['portfolio_total'] = SPY_signals['portfolio_cash'] + SPY_signals['portfolio_holdings']

In [25]:
# Calculate the portfolio daily returns
SPY_signals['portfolio_daily_returns'] = SPY_signals['portfolio_total'].pct_change()

In [26]:
# Calculate the portfolio cumulative returns
SPY_signals['portfolio_cumulative_returns'] = (1 + SPY_signals['portfolio_daily_returns']).cumprod() - 1

In [27]:
SPY_signals.head(10).dropna()

close   returns   SMA_Fast   SMA_Slow  signal  \
Date                                                           
1993-02-16  43.46875 -0.025228  44.557292  44.680556     0.0   
1993-02-17  43.43750 -0.000719  44.302083  44.527778     0.0   
1993-02-18  43.40625 -0.000719  44.093750  44.350694     0.0   
1993-02-19  43.56250  0.003600  43.901042  44.194444     0.0   
1993-02-22  43.71875  0.003587  43.697917  44.055556     1.0   
1993-02-23  43.68750 -0.000715  43.546875  43.947917     1.0   
1993-02-24  44.25000  0.012876  43.677083  43.895833     1.0   
1993-02-25  44.34375  0.002119  43.828125  43.829861     1.0   

            strategy_returns  entry/exit  position  entry/exit_position  \
Date                                                                      
1993-02-16         -0.000000         0.0       0.0                  0.0   
1993-02-17         -0.000000         0.0       0.0                  0.0   
1993-02-18         -0.000000         0.0       0.0                  0.0   
1993-02-19          0.000000         0.0       0.0                  0.0   
1993-02-22          0.000000         1.0    5000.0               5000.0   
1993-02-23         -0.000715         0.0    5000.0                  0.0   
1993-02-24          0.012876         0.0    5000.0                  0.0   
1993-02-25          0.002119         0.0    5000.0                  0.0   

            portfolio_holdings  portfolio_cash  portfolio_total  \
Date                                                              
1993-02-16                0.00      1000000.00       1000000.00   
1993-02-17                0.00      1000000.00       1000000.00   
1993-02-18                0.00      1000000.00       1000000.00   
1993-02-19                0.00      1000000.00       1000000.00   
1993-02-22           218593.75       781406.25       1000000.00   
1993-02-23           218437.50       781406.25        999843.75   
1993-02-24           221250.00       781406.25       1002656.25   
1993-02-25           221718.75       781406.25       1003125.00   

            portfolio_daily_returns  portfolio_cumulative_returns  
Date                                                               
1993-02-16                 0.000000                      0.000000  
1993-02-17                 0.000000                      0.000000  
1993-02-18                 0.000000                      0.000000  
1993-02-19                 0.000000                      0.000000  
1993-02-22                 0.000000                      0.000000  
1993-02-23                -0.000156                     -0.000156  
1993-02-24                 0.002813                      0.002656  
1993-02-25                 0.000468                      0.003125

In [28]:
# Visualize exit position relative to total portfolio value
exit = SPY_signals[SPY_signals['entry/exit'] == -1.0]['portfolio_total'].hvplot.scatter(
    color='red',
    marker='v',
    legend=False,
    ylabel='total_portfolio_value',
    width=1000,
    height=400
)

# Visualize entry position relative to total portfolio value
entry = SPY_signals[SPY_signals['entry/exit'] == 1.0]['portfolio_total'].hvplot.scatter(
    color='green',
    marker='^',
    ylabel='total_portfolio_value',
    width=1000,
    height=400
)

# Visualize the value of the total portfolio
total_portfolio_value = SPY_signals[['portfolio_total']].hvplot(
    line_color='yellow',
    ylabel='total_portfolio_value',
    xlabel='Date',
    width=1000,
    height=400
)

# Overlay the plots
portfolio_entry_exit_plot = total_portfolio_value * entry * exit
portfolio_entry_exit_plot.opts(
    title="SPY Algorithm - Total Portfolio Value",
    yformatter='%.0f'
)

:Overlay
   .Curve.I                    :Curve   [Date]   (portfolio_total)
   .Scatter.Portfolio_total.I  :Scatter   [Date]   (portfolio_total)
   .Scatter.Portfolio_total.II :Scatter   [Date]   (portfolio_total)

In [29]:
display(SPY_signals.head())
display(SPY_signals.tail())

close   returns   SMA_Fast   SMA_Slow  signal  \
Date                                                           
1993-02-11  44.93750  0.004892  44.875000  44.739583     0.0   
1993-02-12  44.59375 -0.007650  44.807292  44.777778     0.0   
1993-02-16  43.46875 -0.025228  44.557292  44.680556     0.0   
1993-02-17  43.43750 -0.000719  44.302083  44.527778     0.0   
1993-02-18  43.40625 -0.000719  44.093750  44.350694     0.0   

            strategy_returns  entry/exit  position  entry/exit_position  \
Date                                                                      
1993-02-11               NaN         NaN       0.0                  NaN   
1993-02-12              -0.0         0.0       0.0                  0.0   
1993-02-16              -0.0         0.0       0.0                  0.0   
1993-02-17              -0.0         0.0       0.0                  0.0   
1993-02-18              -0.0         0.0       0.0                  0.0   

            portfolio_holdings  portfolio_cash  portfolio_total  \
Date                                                              
1993-02-11                 0.0             NaN              NaN   
1993-02-12                 0.0       1000000.0        1000000.0   
1993-02-16                 0.0       1000000.0        1000000.0   
1993-02-17                 0.0       1000000.0        1000000.0   
1993-02-18                 0.0       1000000.0        1000000.0   

            portfolio_daily_returns  portfolio_cumulative_returns  
Date                                                               
1993-02-11                      NaN                           NaN  
1993-02-12                      NaN                           NaN  
1993-02-16                      0.0                           0.0  
1993-02-17                      0.0                           0.0  
1993-02-18                      0.0                           0.0

close   returns    SMA_Fast    SMA_Slow  signal  \
Date                                                               
2021-09-03  453.079987 -0.000243  452.018331  450.583333     0.0   
2021-09-07  451.459991 -0.003576  452.219996  450.971110     0.0   
2021-09-08  450.910004 -0.001218  451.999995  451.193332     0.0   
2021-09-09  448.980011 -0.004280  451.569997  451.495555     0.0   
2021-09-10  445.440002 -0.007885  450.510000  450.961110     1.0   

            strategy_returns  entry/exit  position  entry/exit_position  \
Date                                                                      
2021-09-03              -0.0         0.0       0.0                  0.0   
2021-09-07              -0.0         0.0       0.0                  0.0   
2021-09-08              -0.0         0.0       0.0                  0.0   
2021-09-09              -0.0         0.0       0.0                  0.0   
2021-09-10              -0.0         1.0    5000.0               5000.0   

            portfolio_holdings  portfolio_cash  portfolio_total  \
Date                                                              
2021-09-03                0.00     2827068.415      2827068.415   
2021-09-07                0.00     2827068.415      2827068.415   
2021-09-08                0.00     2827068.415      2827068.415   
2021-09-09                0.00     2827068.415      2827068.415   
2021-09-10          2227200.01      599868.405      2827068.415   

            portfolio_daily_returns  portfolio_cumulative_returns  
Date                                                               
2021-09-03                      0.0                      1.827068  
2021-09-07                      0.0                      1.827068  
2021-09-08                      0.0                      1.827068  
2021-09-09                      0.0                      1.827068  
2021-09-10                      0.0                      1.827068

In [30]:
# Read in the CSV data for QQQ

QQQ_df = pd.read_csv(Path('./Resources/QQQ.csv'),
                     index_col='Date',
                     parse_dates=True,
                     infer_datetime_format=True)

QQQ_df.head()

Open    Close
Date                         
1999-03-10  51.12500  51.0625
1999-03-11  51.43750  51.3125
1999-03-12  51.12500  50.0625
1999-03-15  50.43750  51.5000
1999-03-16  51.71875  51.9375

In [31]:
# Create df for QQQ closing prices

QQQ_close = pd.DataFrame()

QQQ_close['close'] = QQQ_df['Close']


# Review QQQ DF

display(QQQ_close.head())
display(QQQ_close.tail())



close
Date               
1999-03-10  51.0625
1999-03-11  51.3125
1999-03-12  50.0625
1999-03-15  51.5000
1999-03-16  51.9375

close
Date                  
2021-09-03  381.570007
2021-09-07  382.109985
2021-09-08  380.779999
2021-09-09  379.470001
2021-09-10  376.589996

In [32]:
# Create new QQQ DF for signals and calculate daily returns

QQQ_signals = pd.DataFrame()


QQQ_signals['close'] = QQQ_close['close']
QQQ_signals['returns'] = QQQ_close['close'].pct_change()

QQQ_signals = QQQ_signals.dropna()

QQQ_signals.head()

close   returns
Date                         
1999-03-11  51.3125  0.004896
1999-03-12  50.0625 -0.024361
1999-03-15  51.5000  0.028714
1999-03-16  51.9375  0.008495
1999-03-17  51.5625 -0.007220

In [33]:
# Generate simple moving averages for QQQ signals

# Set the short window and long window
short_window = 6
long_window = 9

# Generate the fast and slow simple moving averages 
QQQ_signals['SMA_Fast'] = QQQ_signals['close'].rolling(window=short_window).mean()
QQQ_signals['SMA_Slow'] = QQQ_signals['close'].rolling(window=long_window).mean()

QQQ_signals = QQQ_signals.dropna()

# Review the DataFrame
display(QQQ_signals.head())
display(QQQ_signals.tail())



close   returns   SMA_Fast   SMA_Slow
Date                                                
1999-03-23  48.81250 -0.035207  51.114583  51.062500
1999-03-24  50.46875  0.033931  50.869792  50.968750
1999-03-25  52.31250  0.036533  50.994792  51.218750
1999-03-26  51.75000 -0.010753  50.859375  51.246528
1999-03-29  53.62500  0.036232  51.260417  51.434028

close   returns    SMA_Fast    SMA_Slow
Date                                                    
2021-09-03  381.570007  0.003076  379.800003  377.821113
2021-09-07  382.109985  0.001415  380.811666  378.681112
2021-09-08  380.779999 -0.003481  380.898331  379.345557
2021-09-09  379.470001 -0.003440  380.818329  380.128889
2021-09-10  376.589996 -0.007590  380.153330  380.189999

In [34]:
QQQ_signals["signal"] = 0.0
# Generate the trading signal 0 or 1,
# where 1 is the short-window (SMA6) greater than the long-window (SMA9)
# and 0 is when the condition is not met
QQQ_signals["signal"][short_window:] = np.where(
    QQQ_signals["SMA_Slow"][short_window:] > QQQ_signals["SMA_Fast"][short_window:], 1.0, 0.0
)

# Review the DataFrame
QQQ_signals.tail(10)

close   returns    SMA_Fast    SMA_Slow  signal
Date                                                            
2021-08-27  376.040009  0.009720  373.098338  370.054447     0.0
2021-08-30  380.260010  0.011222  375.186671  371.668891     0.0
2021-08-31  379.950012 -0.000815  376.306671  373.640004     0.0
2021-09-01  380.579987  0.001658  377.341670  375.486671     0.0
2021-09-02  380.399994 -0.000473  378.275004  376.894447     0.0
2021-09-03  381.570007  0.003076  379.800003  377.821113     0.0
2021-09-07  382.109985  0.001415  380.811666  378.681112     0.0
2021-09-08  380.779999 -0.003481  380.898331  379.345557     0.0
2021-09-09  379.470001 -0.003440  380.818329  380.128889     0.0
2021-09-10  376.589996 -0.007590  380.153330  380.189999     1.0

In [35]:
# Initiate the value count

QQQ_signals['signal'].value_counts()

0.0    3303
1.0    2353
Name: signal, dtype: int64

In [36]:
# Calculate the strategy returns and add them to the signals_df DataFrame
QQQ_signals['strategy_returns'] = QQQ_signals['returns'] * QQQ_signals['signal'].shift()

# Review the DataFrame
display(QQQ_signals.head())
display(QQQ_signals.tail())

close   returns   SMA_Fast   SMA_Slow  signal  strategy_returns
Date                                                                          
1999-03-23  48.81250 -0.035207  51.114583  51.062500     0.0               NaN
1999-03-24  50.46875  0.033931  50.869792  50.968750     0.0               0.0
1999-03-25  52.31250  0.036533  50.994792  51.218750     0.0               0.0
1999-03-26  51.75000 -0.010753  50.859375  51.246528     0.0              -0.0
1999-03-29  53.62500  0.036232  51.260417  51.434028     0.0               0.0

close   returns    SMA_Fast    SMA_Slow  signal  \
Date                                                               
2021-09-03  381.570007  0.003076  379.800003  377.821113     0.0   
2021-09-07  382.109985  0.001415  380.811666  378.681112     0.0   
2021-09-08  380.779999 -0.003481  380.898331  379.345557     0.0   
2021-09-09  379.470001 -0.003440  380.818329  380.128889     0.0   
2021-09-10  376.589996 -0.007590  380.153330  380.189999     1.0   

            strategy_returns  
Date                          
2021-09-03               0.0  
2021-09-07               0.0  
2021-09-08              -0.0  
2021-09-09              -0.0  
2021-09-10              -0.0

In [37]:
(1 + QQQ_signals[['strategy_returns','returns']]).cumprod().hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [38]:
# Calculate the points in time when the Signal value changes
# Identify trade entry (1) and exit (-1) points
QQQ_signals["entry/exit"] = QQQ_signals["signal"].diff()

# Review the DataFrame
QQQ_signals.loc["2020-02-09":"2020-02-17"]

close   returns    SMA_Fast    SMA_Slow  signal  \
Date                                                               
2020-02-10  231.970001  0.012086  228.238334  225.878891     0.0   
2020-02-11  232.009995  0.000172  229.843333  227.012224     0.0   
2020-02-12  234.270004  0.009741  230.976667  228.308890     0.0   
2020-02-13  233.970001 -0.001281  231.935000  229.964445     0.0   
2020-02-14  234.639999  0.002864  232.676666  231.326667     0.0   

            strategy_returns  entry/exit  
Date                                      
2020-02-10               0.0         0.0  
2020-02-11               0.0         0.0  
2020-02-12               0.0         0.0  
2020-02-13              -0.0         0.0  
2020-02-14               0.0         0.0

In [39]:
# Set initial capital for backtesting
initial_capital_qqq = float(1000000)

# Set the share size
share_size_qqq = 5000

In [40]:
# Buy a 5000 share position when the dual moving average crossover Signal equals 1 (SMA6 is greater than SMA9)
# Sell a 5000 share position when the dual moving average crossover Signal equals 0 (SMA6 is less than SMA9)
QQQ_signals['position'] = share_size_qqq * QQQ_signals['signal']

In [41]:
# Determine the points in time where a 5000 share position is bought or sold
QQQ_signals['entry/exit_position'] = QQQ_signals['position'].diff()

In [42]:
# Multiply the close price by the number of shares held, or the Position
QQQ_signals['portfolio_holdings'] = QQQ_signals['close'] * QQQ_signals['position']

In [43]:
# Subtract the amount of either the cost or proceeds of the trade from the initial capital invested
QQQ_signals['portfolio_cash'] = initial_capital_qqq - (QQQ_signals['close'] * QQQ_signals['entry/exit_position']).cumsum()

In [44]:
# Calculate the total portfolio value by adding the portfolio cash to the portfolio holdings (or investments)
QQQ_signals['portfolio_total'] = QQQ_signals['portfolio_cash'] + QQQ_signals['portfolio_holdings']

In [45]:
# Calculate the portfolio daily returns
QQQ_signals['portfolio_daily_returns'] = QQQ_signals['portfolio_total'].pct_change()

In [46]:
# Calculate the portfolio cumulative returns
QQQ_signals['portfolio_cumulative_returns'] = (1 + QQQ_signals['portfolio_daily_returns']).cumprod() - 1

In [47]:
display(QQQ_signals.head(10).dropna())
display(QQQ_signals.tail())

close   returns   SMA_Fast   SMA_Slow  signal  \
Date                                                            
1999-03-25  52.312500  0.036533  50.994792  51.218750     0.0   
1999-03-26  51.750000 -0.010753  50.859375  51.246528     0.0   
1999-03-29  53.625000  0.036232  51.260417  51.434028     0.0   
1999-03-30  53.250000 -0.006993  51.703125  51.621528     0.0   
1999-03-31  52.468750 -0.014671  52.312500  51.611111     0.0   
1999-04-01  53.562500  0.020846  52.828125  51.871528     0.0   
1999-04-05  55.500000  0.036173  53.359375  52.416667     0.0   
1999-04-06  55.609375  0.001971  54.002604  53.171875     0.0   

            strategy_returns  entry/exit  position  entry/exit_position  \
Date                                                                      
1999-03-25               0.0         0.0       0.0                  0.0   
1999-03-26              -0.0         0.0       0.0                  0.0   
1999-03-29               0.0         0.0       0.0                  0.0   
1999-03-30              -0.0         0.0       0.0                  0.0   
1999-03-31              -0.0         0.0       0.0                  0.0   
1999-04-01               0.0         0.0       0.0                  0.0   
1999-04-05               0.0         0.0       0.0                  0.0   
1999-04-06               0.0         0.0       0.0                  0.0   

            portfolio_holdings  portfolio_cash  portfolio_total  \
Date                                                              
1999-03-25                 0.0       1000000.0        1000000.0   
1999-03-26                 0.0       1000000.0        1000000.0   
1999-03-29                 0.0       1000000.0        1000000.0   
1999-03-30                 0.0       1000000.0        1000000.0   
1999-03-31                 0.0       1000000.0        1000000.0   
1999-04-01                 0.0       1000000.0        1000000.0   
1999-04-05                 0.0       1000000.0        1000000.0   
1999-04-06                 0.0       1000000.0        1000000.0   

            portfolio_daily_returns  portfolio_cumulative_returns  
Date                                                               
1999-03-25                      0.0                           0.0  
1999-03-26                      0.0                           0.0  
1999-03-29                      0.0                           0.0  
1999-03-30                      0.0                           0.0  
1999-03-31                      0.0                           0.0  
1999-04-01                      0.0                           0.0  
1999-04-05                      0.0                           0.0  
1999-04-06                      0.0                           0.0

close   returns    SMA_Fast    SMA_Slow  signal  \
Date                                                               
2021-09-03  381.570007  0.003076  379.800003  377.821113     0.0   
2021-09-07  382.109985  0.001415  380.811666  378.681112     0.0   
2021-09-08  380.779999 -0.003481  380.898331  379.345557     0.0   
2021-09-09  379.470001 -0.003440  380.818329  380.128889     0.0   
2021-09-10  376.589996 -0.007590  380.153330  380.189999     1.0   

            strategy_returns  entry/exit  position  entry/exit_position  \
Date                                                                      
2021-09-03               0.0         0.0       0.0                  0.0   
2021-09-07               0.0         0.0       0.0                  0.0   
2021-09-08              -0.0         0.0       0.0                  0.0   
2021-09-09              -0.0         0.0       0.0                  0.0   
2021-09-10              -0.0         1.0    5000.0               5000.0   

            portfolio_holdings  portfolio_cash  portfolio_total  \
Date                                                              
2021-09-03                0.00      2037656.30        2037656.3   
2021-09-07                0.00      2037656.30        2037656.3   
2021-09-08                0.00      2037656.30        2037656.3   
2021-09-09                0.00      2037656.30        2037656.3   
2021-09-10          1882949.98       154706.32        2037656.3   

            portfolio_daily_returns  portfolio_cumulative_returns  
Date                                                               
2021-09-03                      0.0                      1.037656  
2021-09-07                      0.0                      1.037656  
2021-09-08                      0.0                      1.037656  
2021-09-09                      0.0                      1.037656  
2021-09-10                      0.0                      1.037656

In [48]:
# Visualize exit position relative to total portfolio value
exit_qqq = QQQ_signals[QQQ_signals['entry/exit'] == -1.0]['portfolio_total'].hvplot.scatter(
    color='yellow',
    marker='v',
    legend=False,
    ylabel='total_portfolio_value',
    width=1000,
    height=400
)

# Visualize entry position relative to total portfolio value
entry_qqq = QQQ_signals[QQQ_signals['entry/exit'] == 1.0]['portfolio_total'].hvplot.scatter(
    color='purple',
    marker='^',
    ylabel='total_portfolio_value',
    width=1000,
    height=400
)

# Visualize the value of the total portfolio
total_portfolio_value_qqq = QQQ_signals[['portfolio_total']].hvplot(
    line_color='green',
    ylabel='total_portfolio_value',
    xlabel='Date',
    width=1000,
    height=400
)

# Overlay the plots
portfolio_entry_exit_plot_qqq = total_portfolio_value_qqq * entry_qqq * exit_qqq
portfolio_entry_exit_plot_qqq.opts(
    title="QQQ Algorithm - Total Portfolio Value",
    yformatter='%.0f'
)

:Overlay
   .Curve.I                    :Curve   [Date]   (portfolio_total)
   .Scatter.Portfolio_total.I  :Scatter   [Date]   (portfolio_total)
   .Scatter.Portfolio_total.II :Scatter   [Date]   (portfolio_total)

---

### Generating the Features and Target Sets

#### Create the features set

In [49]:
# Assign a copy of the sma_fast and sma_slow columns to a new DataFrame called X
X = SPY_signals[['SMA_Fast', 'SMA_Slow']].copy()

# Display sample data
display(X.head())
display(X.tail())

SMA_Fast   SMA_Slow
Date                            
1993-02-11  44.875000  44.739583
1993-02-12  44.807292  44.777778
1993-02-16  44.557292  44.680556
1993-02-17  44.302083  44.527778
1993-02-18  44.093750  44.350694

SMA_Fast    SMA_Slow
Date                              
2021-09-03  452.018331  450.583333
2021-09-07  452.219996  450.971110
2021-09-08  451.999995  451.193332
2021-09-09  451.569997  451.495555
2021-09-10  450.510000  450.961110

#### Create the target set

In [50]:
# Create a new column in the SPY_signals called signal setting its value to zero.
SPY_signals['signal'] = 0.0

In [51]:
# Create the signal to buy
SPY_signals.loc[(SPY_signals['returns'] >= 0), 'signal'] = 1

In [52]:
# Create the signal to sell
SPY_signals.loc[(SPY_signals['returns'] < 0), 'signal'] = -1

In [53]:
# Copy the new signal column to a new Series called y.
y = SPY_signals['signal'].copy()

display(y.head())
display(y.tail())

Date
1993-02-11    1.0
1993-02-12   -1.0
1993-02-16   -1.0
1993-02-17   -1.0
1993-02-18   -1.0
Name: signal, dtype: float64

Date
2021-09-03   -1.0
2021-09-07   -1.0
2021-09-08   -1.0
2021-09-09   -1.0
2021-09-10   -1.0
Name: signal, dtype: float64

---

### Split the Data Into Training and Testing Datasets

#### Creating the Training Datasets

In [54]:
# Imports 
from pandas.tseries.offsets import DateOffset

In [55]:
# Select the start of the training period
training_begin = X.index.min()

# Display the training begin date
print(training_begin)

1993-02-11 00:00:00


In [56]:
# Select the ending period for the training data with an offset of 3 months
training_end = X.index.min() + DateOffset(months=1)

# Display the training end date
print(training_end)

1993-03-11 00:00:00


In [57]:
# Generate the X_train and y_train DataFrames
X_train = X.loc[training_begin:training_end]
y_train = y.loc[training_begin:training_end]

# Display sample data
X_train.head()

SMA_Fast   SMA_Slow
Date                            
1993-02-11  44.875000  44.739583
1993-02-12  44.807292  44.777778
1993-02-16  44.557292  44.680556
1993-02-17  44.302083  44.527778
1993-02-18  44.093750  44.350694

In [58]:
# Generate the X_test and y_test DataFrames
X_test = X.loc[training_end:]
y_test = y.loc[training_end:]

# Display sample data
X_test.head()

SMA_Fast   SMA_Slow
Date                            
1993-03-11  45.369792  45.173611
1993-03-12  45.406250  45.263889
1993-03-15  45.500000  45.305556
1993-03-16  45.427083  45.326389
1993-03-17  45.333333  45.343750

#### Standardizing the Data

In [59]:
# Imports
from sklearn.preprocessing import StandardScaler

In [60]:
# Create a StandardScaler instance
scaler = StandardScaler()
 
# Apply the scaler model to fit the X-train data
X_scaler = scaler.fit(X_train)
 
# Transform the X_train and X_test DataFrames using the X_scaler
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

---

### Incorporate the SVM Machine Learning Into the Trading Strategy

In [61]:
# Imports
from sklearn import svm
from sklearn.metrics import classification_report

In [62]:
# Create the classifier model
svm_model = svm.SVC()
 
# Fit the model to the data using X_train_scaled and y_train
svm_model = svm_model.fit(X_train_scaled, y_train)

# Use the trained model to predict the trading signals for the training data
training_signal_predictions = svm_model.predict(X_train_scaled)

# Display the sample predictions
training_signal_predictions[:10]

array([-1., -1., -1., -1., -1.,  1.,  1.,  1.,  1.,  1.])

In [63]:
# Evaluate the model using a classification report
training_report = classification_report(y_train, training_signal_predictions)
print(training_report)

              precision    recall  f1-score   support

        -1.0       0.67      0.80      0.73        10
         1.0       0.75      0.60      0.67        10

    accuracy                           0.70        20
   macro avg       0.71      0.70      0.70        20
weighted avg       0.71      0.70      0.70        20



---

### Backtesting a Machine Learning Trading Algorithm

In [64]:
# Use the trained model to predict the trading signals for the testing data.
testing_signal_predictions = svm_model.predict(X_test_scaled)

In [65]:
# Evaluate the model's ability to predict the trading signal for the testing data
svm_testing_report = classification_report(y_test, testing_signal_predictions)
print(svm_testing_report)

              precision    recall  f1-score   support

        -1.0       0.46      1.00      0.63      3273
         1.0       0.75      0.00      0.00      3906

    accuracy                           0.46      7179
   macro avg       0.60      0.50      0.31      7179
weighted avg       0.62      0.46      0.29      7179



In [66]:
# Create a new empty predictions DataFrame using code provided below.
predictions_df = pd.DataFrame(index=X_test.index)
predictions_df["predicted_signal"] = testing_signal_predictions
predictions_df["actual_returns"] = SPY_signals["returns"]
predictions_df["trading_algorithm_returns"] = predictions_df["actual_returns"] * predictions_df["predicted_signal"]
predictions_df.head()

predicted_signal  actual_returns  trading_algorithm_returns
Date                                                                   
1993-03-11              -1.0       -0.002736                   0.002736
1993-03-12              -1.0       -0.010288                   0.010288
1993-03-15              -1.0        0.004851                  -0.004851
1993-03-16              -1.0        0.000000                  -0.000000
1993-03-17              -1.0       -0.006207                   0.006207

In [67]:
# Calculate and plot the cumulative returns for the `actual_returns` and the `trading_algorithm_returns`
(1 + predictions_df[["actual_returns", "trading_algorithm_returns"]]).cumprod().plot()

<AxesSubplot:xlabel='Date'>

---

# Add a New Machine Learning Model

## Step 2: Import the `LogisticRegression` model from scikit-learn.


In [68]:
# Import LogisticRegression from sklearn
from sklearn.linear_model import LogisticRegression

In [69]:
# Create an instance of the LogisticRegression model
logistic_regression_model = LogisticRegression()

## Step 3: Using the same training data that the SVM model used (`X_train_scaled` and `y_train`), fit the `LogisticRegression` model.

In [70]:
# Fit the LogisticRegression model
logistic_regression_model.fit(X_train_scaled, y_train)

LogisticRegression()

## Step 4: Use the trained model to predict the trading signals for the training data. Use the `classification_report` module to evaluate the model.

In [71]:
# Use the trained LogisticRegression model to predict the trading signals for the training data
lr_training_signal_predictions = logistic_regression_model.predict(X_train_scaled)

# Diplay the predictions
lr_training_signal_predictions

array([-1., -1., -1., -1., -1.,  1.,  1.,  1.,  1.,  1.,  1.,  1.,  1.,
        1.,  1., -1., -1., -1., -1., -1.])

In [72]:
# Generate a classification report using the training data and the logistic regression model's predications
lr_training_report = classification_report(y_train, lr_training_signal_predictions)

# Review the classification report
print(lr_training_report)

              precision    recall  f1-score   support

        -1.0       0.70      0.70      0.70        10
         1.0       0.70      0.70      0.70        10

    accuracy                           0.70        20
   macro avg       0.70      0.70      0.70        20
weighted avg       0.70      0.70      0.70        20



## Step 5: Backtest the `LogisticRegression` model using the testing data to evaluate its performance.


In [73]:
# Use the trained model to predict the trading signals for the testing data.
lr_testing_signal_predictions = logistic_regression_model.predict(X_test_scaled)

In [74]:
# Generate a classification report using the testing data and the logistic regression model's predictions
lr_testing_report = classification_report(y_test, lr_testing_signal_predictions)

# Review the testing classification report
print(lr_testing_report)

              precision    recall  f1-score   support

        -1.0       0.46      1.00      0.63      3273
         1.0       0.71      0.00      0.01      3906

    accuracy                           0.46      7179
   macro avg       0.59      0.50      0.32      7179
weighted avg       0.60      0.46      0.29      7179



## Step 6: Compare the performance of the logistic regression and SVM models using the classification reports generated with the testing data. 

In [75]:
# Print the classification report for the Logistic Regression model using the test data
print("Logistic Regression Classification Report")
print(lr_testing_report)

Logistic Regression Classification Report
              precision    recall  f1-score   support

        -1.0       0.46      1.00      0.63      3273
         1.0       0.71      0.00      0.01      3906

    accuracy                           0.46      7179
   macro avg       0.59      0.50      0.32      7179
weighted avg       0.60      0.46      0.29      7179



In [76]:
# Print the classification report for the SVM model using the test data
print("SVM Classification Report")
print(svm_testing_report)

SVM Classification Report
              precision    recall  f1-score   support

        -1.0       0.46      1.00      0.63      3273
         1.0       0.75      0.00      0.00      3906

    accuracy                           0.46      7179
   macro avg       0.60      0.50      0.31      7179
weighted avg       0.62      0.46      0.29      7179

